In [1]:
import pandas as pd
import requests
import time
import urllib.parse as urlparse

In [2]:
BASE_URL = "https://ps6bzj7vlp0okc-3754.proxy.runpod.net/"

In [3]:
def txt2img(prompt: str, name: str):
    while True:
        try:
            url = urlparse.urljoin(BASE_URL, "txt2img")
            payload = {
                "prompt": prompt,
                "negative_prompt": None,
                "width": "1024",
                "height": "1024",
                "samples": 1,
                "num_inference_steps": "8",
                "seed": 1337,
                "guidance_scale": 3,
                "safety_checker": "no",
            }

            headers = {"Content-Type": "application/x-www-form-urlencoded"}

            response = requests.post(url, headers=headers, data=payload)
            response_json = response.json()
            link = response_json["links"][0]

            time.sleep(2)

            response = requests.get(link, stream=True)
            
            while b"<!DOCTYPE" in response.content:
                time.sleep(1)
                response = requests.get(link, stream=True)
            
            with open(f"{name}.png", "wb") as file:
                file.write(response.content)
            break
        
        except Exception as e:
            print(f"Exception: {e}")
            time.sleep(2)

In [4]:
df = pd.read_csv("PartiPrompts.tsv", sep="\t")

In [5]:
df.fillna("", inplace=True)

In [6]:
df

Prompt        Category  \
0                                                bond        Abstract   
1                                             element        Abstract   
2                                            molecule        Abstract   
3                                                life        Abstract   
4                                             protein        Abstract   
...                                               ...             ...   
1627   a wooden post with a yellow '3' painted on top  Outdoor Scenes   
1628  a wooden post in front of a patch of tall grass  Outdoor Scenes   
1629     a wooden post with a blue '5' painted on top  Outdoor Scenes   
1630     a series of musical notes on a black t-shirt       Artifacts   
1631   a series of musical notes on a computer screen       Artifacts   

              Challenge                                              Note  
0                 Basic  Biology-inspired concepts with multiple meanings  
1                 Basic  Biology-inspired concepts with multiple meanings  
2                 Basic  Biology-inspired concepts with multiple meanings  
3                 Basic  Biology-inspired concepts with multiple meanings  
4                 Basic  Biology-inspired concepts with multiple meanings  
...                 ...                                               ...  
1627  Writing & Symbols                                                    
1628  Writing & Symbols                                                    
1629  Writing & Symbols                                                    
1630  Writing & Symbols                                                    
1631  Writing & Symbols                                                    

[1632 rows x 4 columns]

In [ ]:
for index, row in df.iterrows():
    if index <= 1617:
        continue
    index = f"{index:04}"
    prompt = f"{row['Prompt'].lower()}, {row['Category'].lower()}, {row['Note'].lower()}".strip()
    print(f"{index}: {prompt}")
    txt2img(prompt, index)

1611: a black t-shirt with the peace sign on it, artifacts,
1612: a store front with 'grassy meadow' written on it, outdoor scenes,
1613: a store front with 'awesomepurchase' written on it, outdoor scenes,
1614: a laptop screen showing an internet search, artifacts,
1615: a laptop screen showing a bunch of photographs, artifacts,
1616: a laptop screen showing a document being edited, artifacts,
1617: a book with the words 'don't panic!' written on it, artifacts,
